In [43]:
import spacy
from spacy import displacy
from collections import Counter
import en_core_web_sm
#!pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz --user
nlp = en_core_web_sm.load()
import pandas as pd
import json
!pip install bs4 --user
from bs4 import BeautifulSoup
import requests
import re
import os
import mmap
import random
from spacy.gold import GoldParse
from spacy.scorer import Scorer
from spacy.util import minibatch, compounding
import warnings
warnings.filterwarnings('ignore')

You are using pip version 18.0, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


## Load data

In [44]:
with open('data.json', 'r') as f:
    dict_json_weighted = json.load(f)
object_1 = list(dict_json_weighted.keys())[1]
for i in range(len(dict_json_weighted[object_1]['log'])):
    print(str(i)+"-"+dict_json_weighted[object_1]['log'][i]['text'])

0-Can you help me find a guesthouse that includes free parking?
1-Definitely! Do you have a particular price range or area in mind?
2-I need something cheap, but I am hoping for at least 4 stars. Is that possible?
3- We have a guest house that fits your description in the east, the west, and the center. Do you have a preference for location? 
4-How about the guesthouse in the west? Do you know if they offer internet?
5-Yes and free parking as well.
6-Thank you, I also need to know if theres a train that leaves from cambridge after 14:15.
7-Okay! Where are you going?
8-I will be going to Ely.
9-What day are you leaving?
10-I'm sorry, the train I'm looking for should depart Friday and go to London Kings Cross, not Ely.
11-The TR2420 leaves at 15:00 and that's the earliest one I can get for you. 
12-I need 5 tickets for that one. 
13-Booking was successful, the total fee is 118 GBP payable at the station. Reference number is : 71ZIVN5S. Is there anything else I can help with?
14-That is a

## Load ontology

In [45]:
with open('ontology.json', 'r') as o:
    ontology = json.load(o)
    my_ent=list(ontology.keys())
    
    
action=['inform', 'request', 'select', 'recommend', 'not found', 'request booking', 'offer booking', 
        'inform booked', 'decline booking', 'welcome','greet', 'bye', 'reqmore' ]
topic= ['hotel', 'restaurant', 'taxi', 'train', 'attraction', 'police', 'hospital']

## display topics and actions

In [46]:
top=[]
act=[]
ont=list(ontology.keys())
for i in range(len(dict_json_weighted[object_1]['log'])):
    #print(dict_json_weighted[object_1]['log'][i]['text'])
    sentence =nlp (dict_json_weighted[object_1]['log'][i]['text'])
    for x in [y for y in sentence if y.pos_ != 'PUNCT']:
        if str(x).lower() in topic:
            if str(x).lower() not in top:
                top.append(str(x).lower()) 
        if x.lemma_ in action:
            if x.lemma_ not in act:
                act.append(x.lemma_)
        #for z in ont:
            #if str(x) in str(ontology[z]):
                #print(z+" :"+str(x))           
print("topics: "+str(top))
print("actions: "+str(act))


topics: ['train', 'taxi']
actions: ['welcome']


## Display the updated slots 

In [47]:
for i in dict_json_weighted[object_1]['goal']:
    if i not in['message', 'topic']:
        if dict_json_weighted[object_1]['goal'][i] !={}:
            print("****** "+i+" ******")
            for j in (dict_json_weighted[object_1]['goal'][i]):
                if dict_json_weighted[object_1]['goal'][i][j] not in ['fail_info', {}]:
                    print("°"+j)
                    print(dict_json_weighted[object_1]['goal'][i][j])
    

****** hotel ******
°reqt
['address', 'internet']
°info
{'parking': 'yes', 'pricerange': 'cheap', 'type': 'guesthouse', 'stars': '4'}
****** train ******
°book
{'invalid': True, 'people': '5'}
°info
{'departure': 'cambridge', 'leaveAt': '14:15', 'destination': 'london kings cross', 'day': 'friday'}


# Custom NER

### create training sample

In [48]:
Train_data = [
   (
        "Hello, I am looking for a cheap place to dine in the centre", { "entities" :
        [(26, 45, "price-range"), (46, 59, "area")]
        }
    ),(
        "not really but i need it for 3 people",  { "entities" : 
        [(25, 37, "restaurant-book-people")]
        }
    ),(
        "I recommend La Raza - fantastic (and cheap!) Spanish cuisine. I'd be happy to book a table for you, if you like.",  { "entities" : 
        [(12, 20, "restaurant-name"), (37, 42, "price-range"),(45, 60, "restaurant-food")]
        }

    ),(
        "Yes for 3 at 14:45 wednesday, can I get the reference number too please", { "entities" :
        [(4, 9, "restaurant-book-people"), (10, 18, "restaurant-book-time"), (19, 28, "day")]
        }
    ),( 
        "Both offer free parking and free wifi. The Alexander B&B is 4 star rated. The El Shaddai has a 0 rating.", { "entities" : 
             [(11, 23, "hotel-parking"), (28, 37, "hotel-internet"), (39, 56, "hotel-name"), (60, 66, "hotel-stars"), (74, 87, "hotel-name"), (95, 103, "hotel-stars")]
             }
    ),( 
        "3 nights, 3 people, please.", { "entities" : 
             [(0, 8, "hotel-book-stay"), (10, 18, "hotel-book-people")]
             }
    ),( 
        "I would like a taxi from the hotel to the restaurant. I would like to arrive by 14:45. I would like the contact number and car type",  { "entities" : 
             [(77, 85, "taxi-arrive-by")]
             }
    ),( 
        "Thanks. I also need a cheap place to stay in the center.", { "entities" : 
             [(22, 33, "price-range"),(42, 55, "area")]
             }
    ),( 
        "I am looking for info about a hotel called city centre north b and b. Can you help?", { "entities" : 
             [(43, 68, "hotel-name")]
             }
    ),( 
        "Yes. City Centre North B and B is a guesthouse in the north side of town, that has both free internet and parking. Do you want to book a room?", { "entities" : 
             [(5,30, "hotel-name"),(34, 46, "hotel-type"),(47, 72, "area")]
             }
    ),( 
        "Ok, I am also looking for a train from Cambridge to Bishops Stortford.", { "entities" : 
             [(34, 48, "train-departure"),(49, 69, "train-destination")]
             }
    ),( 
        "I'll be leaving Monday after 15:30.", { "entities" : 
             [(16, 22, "day"),(23, 34, "train-leave-at")]
             }
    ),( 
        "TR2630 leaves at 17:29. Would you like for me to book the train for you?", { "entities" : 
             [(14, 22, "train-leave-at")]
             }
    ),( 
        "Yes I would like to book the train for 4 people and I'll need the reference number please.", { "entities" : 
             [(35, 47, "train-book-people")]
             }
    ),( 
        "I'm looking for a Mediterranean restaurant near the centre of town.", { "entities" : 
             [(18, 42, "restaurant-food"), (43, 66, "area")]
             }
    ),( 
        "I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?", { "entities" : 
             [(37, 49, "restaurant-name"),(51, 60, "restaurant-name"),(65, 72, "restaurant-name")]
             }
    ),( 
        "Great, could I book a table of 5 for 11:30 on wednesday? If so, please provide me with a reference number", { "entities" : 
             [(20, 32, "restaurant-book-people"),(33, 42, "restaurant-book-time"),(43, 55, "restaurant-bookday")]
             }
    ),( 
        "Is one of them in the cheap price range? ", { "entities" : 
             [(15, 39, "price-range")]
             }
    ),( 
        "Yes. Can you please search for an attraction in the type of college?", { "entities" : 
             [(45, 67, "attraction-type")]
             }
    ),( 
        "Is an entrance fee okay? If so, the corpus christi college located at king's parade. Fee is 2 pounds. Would you like the phone number? ", { "entities" : 
             [(32, 58, "attraction-name")]
             }
    ),( 
        "I would like to leave Corpus Christi College in enough time to arrive at the restaurant at the booked time of 11:30. ", { "entities" : 
             [(22, 44, "train-departure"), (88, 130, "train-arrive-by")]
             }
    ),( 
        "I'm looking for a place to stay in Cambridge. It should include free wifi and be a 3 star.  Can you help me please? ", { "entities" : 
             [(64, 73, "hotel-internet"), (78, 89, "hotel-stars")]
             }
    ),( 
        "There are five to choose from. Would you like moderate or expensive price point? ", { "entities" : 
             [(46, 67, "price-range")]
             }
    ),( 
        "I have the gonville hotel. It is expensive. Would you like me to book that for you?", { "entities" : 
             [(7, 25, "hotel-name"), (33, 42, "price-range")]
             }
    ),( 
        "Do they have free parking? If so, please reserve a room for Tuesday for 7 people, 4 nights.", { "entities" : 
             [(13, 25, "hotel-parking"), (56, 67, "day"), (68, 80, "hotel-book-people"), (81,89, "hotel-book-stay")]
             }
    ),( 
        "I am looking for a hotel called The Cambridge Belfry. Can you help me with this? ", { "entities" : 
             [(32, 45, "hotel-name")]
             }
    ),( 
        "Yes, thank you. I'd also like to find a swimming pool in the town centre. ", { "entities" : 
             [(40, 53, "attraction-type"), (57, 75, "attraction-area")]
             }
    ),( 
        "Yes, can you please help me book a taxi to leave the hotel by 03:15", { "entities" : 
             [(59, 69, "taxi-leave-at")]
             }
    ),( 
        "I am looking for a restaurant in the moderate price range that serves Indian food", { "entities" : 
             [(30, 57, "price-range"), (70, 81, "restaurant-food")]
             }
    ),( 
        "Curry prince is an indian restaurant, in the moderate price range and in the east.", { "entities" : 
             [(0, 12, "restaurant-name"), (13, 36, "restaurant-food"), (38, 65, "price-range" ), (70, 81,"area") ]
             }
    ),( 
        "Rajmahal is an Indian restaurant in the east part of town and in the moderate price range. ", { "entities" : 
             [(15, 32, "restaurant-food"), (33, 57, "area"), (62, 89, "price-range")]
             }
    ),( 
        "I want a train that leaves on Monday", { "entities" : 
             [(30, 36, "day")]
             }
    ),( 
        "I would like to travel from Norwich to Cambridge. Are there any leaving after 21:00? ", { "entities" : 
             [(23, 36, "train-departure"), (36,48, "train-destination"), (72,83, "train-leave-at")]
             }
    ),( 
        "it should arrive by 22:35 ", { "entities" : 
             [(17, 25, "train-arrive-by")]
             }
    ),( 
        "No thanks but could you help me find a good college to visit on the south side of town? ", { "entities" : 
             [(44, 51, "attraction-type"), (61,86,"area")]
             }
    ),( 
        "How about a theater in the south? ", { "entities" : 
             [(10, 18, "attraction-type"), (20, 32, "area")]
             }
    ),( 
        "The junction theatre is the only one that meets your specified critera. ", { "entities" : 
             [(0, 21, "attraction-name")]
             }
    ),( 
        "I'm looking for architecture in the centre part of town. Can you help me with that? ", { "entities" : 
             [(16, 29, "attraction-type"), (29, 55, "area")]
             }
    ),( 
        "I personally like Little Saint Mary's Church on Little Saint Mary's Lane.  Admission is free.", { "entities" : 
             [(18, 45, "attraction-name")]
             }
    ),( 
        "Are there any trains going to Cambridge on Friday? ", { "entities" : 
             [(27, 39, "train-departure"), (40,49, "day")]
             }
    ),( 
        "I will be departing from London Kings Cross after 20:45", { "entities" : 
             [(20, 43, "train-departure"), (44,55,"train-leave-at")]
             }
    ),( 
        "There is a 21:17 that will arrive by 22:08.", { "entities" : 
             [(11, 17, "train-leave-at"), (27, 42, "train-arrive-by")]
             }
    ),( 
        "I am looking for a guesthouse to stay at with free wifi please.", { "entities" : 
             [(17, 29, "hotel-type"), (46, 55, "hotel-internet")]
             }
    ),( 
        "I don't care about the price range, either, as long as it is a 4 star guesthouse with free wifi.", { "entities" : 
             [(63, 69, "hotel-stars"), (70, 80, "hotel-type"), (86, 95, "hotel-parking")]
             }
    ),( 
        "No it will be for 2 people for 5 nights.", { "entities" : 
             [(18, 26, "hotel-book-people"), (27, 39,"hotel-book-stay")]
             }
    ),( 
        "Yes! Wandlebury country park is located in south and the entrance fee is free. ", { "entities" : 
             [(5, 29, "attraction-name"), (40, 49, "area")]
             }
    ),( 
        "We don't have any multiple sports facilities in the centre of town. Do you want to look for something else?", { "entities" : 
             [(18, 34, "attraction-type"), (45, 59, "area")]
             }
    ),( 
        "Darrys Cookhouse and Wine Shop is a modern European restaurant located in the centre of town.  It's in the expensive price range.  Would you like to make a reservation? ", { "entities" : 
             [(0, 30, "restaurant-name"), (36, 51, "restaurant-food"),(71,84, "area"), (107,116, "price-range")]
             }
    ),( 
        "Yes, that would be great. I'll need a table for 7 on Friday at 18:00. ", { "entities" : 
             [(36, 49, "restaurant-book-people"), (50, 59, "day"), (60,69, "restaurant-book-time")]
             }
    ),( 
        "Yes, I would like it to be in the north.", { "entities" : 
             [(27,39,"area")]
             }
    ),( 
        "Okay, I would like to recommend the Acorn Guest House.", { "entities" : 
             [(32,41,"hotel-name"),(42,53,"hotel-type")]
             }
    ),( 
        "Please book it for 2 people for 2 nights starting on wednesday, and provide the reference number.  Also, we would like to find an attraction near the hotel.", { "entities" : 
             [(15,28,"hotel-book-people"),(32,40,"hotel-book-stay"),(50,62,"day"),(140,155,"area")]
             }
    ),( 
        "Okay. There are boats, a park, and pools. Would like more information on any of this? ", { "entities" : 
             [(16,21,"attraction-type"),(23,29,"attraction-type"),(35,40,"attraction-type")]
             }
    ),( 
        "I would recommend riverboat georgina. Would you like the address or phone number for that? ", { "entities" : 
             [(18,35,"attraction-name")]
             }
    ),( 
        "I would like to go this Saturday to Cambridge.", { "entities" : 
             [(24,32,"day"),(33,45,"train-destination")]
             }
    ),( 
        "TR4300 will arrive at birmingham new street by 8:44. Would you like to book a ticket?", { "entities" : 
             [(19,43,"train-destination"),(44,51,"train-arrive-by")]
             }
    ),( 
        "A train from Cambridge to Birmingham New Street on Monday will cost 75.10 pounds.", { "entities" : 
             [(8,22,"train-departure"),(23,47,"train-destination"),(48,58,"day")]
             }
    ),( 
        "I'll be leaving from Cambridge on Tuesday. I'd like to get to Leicester by 18:00 please. ", { "entities" : 
             [(16,30,"train-departure"),(31,41,"day"),(59,71,"train-destination"),(72,80,"train-arrive-by")]
             }
    ),( 
        "I would like to book a taxi to the gandhi. ", { "entities" : 
             [(28,41,"taxi-destination")]
             }
    ),( 
        "Hi, I need to get in from King's Lynn to Cambridge ", { "entities" : 
             [(21,37,"train-departure"),(38,50,"train-destination")]
             }
    ),( 
        "How about a museum in the centre? ", { "entities" : 
             [(12,18,"attraction-type"),(19,32,"area")]
             }
    ),( 
        "Yes I am looking for architecture and will need the address, postcode and phone number of the attraction. ", { "entities" : 
             [(21,33,"attraction-type")]
             }
    ),( 
        "How about the holy trinity church? ", { "entities" : 
             [(10,33,"attraction-name")]
             }
    ),( 
        "There are 3 choices, 2 moderately priced and 1 expensive. Do you have a preference? ", { "entities" : 
             [(23,40,"price-range"),(47,56,"price-range")]
             }
    ),( 
        "I need the address and phone number of a restaurant in the center of town that serves Turkish food. Thanks. ", { "entities" : 
             [(52,73,"area"),(86,98,"restaurant-food")]
             }
    ),( 
        "I can suggest Pizza Hut in Fen Ditton located in Cambridge Retail Park Newmarket. ", { "entities" : 
             [(14,23,"restaurant-name"),(46,80,"area")]
             }
    ),( 
        "Yes, could you book me 2 tickets and get me a reference number? ", { "entities" : 
             [(23,32,"train-book-people")]
             }
    ),( 
        "You'll be in a white Skoda and the contact number is 07935 536 503. Can I confirm, though, that you wish to leave the restaurant at 5:15 in the morning? ", { "entities" : 
             [(108,128,"taxi-departure"),(129,136,"taxi-leave-at")]
             }
    ),( 
        "I want to leave on Saturday at any time after 21:15. ", { "entities" : 
             [(16,27,"day"),(40,51,"train-leave-at")]
             }
    ),( 
        "There are 13 colleges in the centre.  King's College and Saint Catharine's College are on the same street and both have free admission.", { "entities" : 
             [(13,21,"attraction-type"),(22,35,"area"),(38,52,"attraction-name"),(57,82,"attraction-name")]
             }
    ),( 
        "the whipple museum of the history of science is an interesting one! ", { "entities" : 
             [(0,19,"attraction-name")]
             }
    ),( 
        "Actually yes! TR5975 leaves from broxbourne at 21:01. It's 14.32 pounds. Does that work? ", { "entities" : 
             [(28,43,"train-departure"),(44,52,"train-leave-at")]
             }
    ),( 
        "Yes. Downing college is free and the phone number is 01223334860. ", { "entities" : 
             [(5,20,"attraction-name")]
             }
    ),( 
        "I am going to Cambridge and i plan to depart from stansted airport and i need a train schedule from stansted airport that will get to Cambridge by 13:30 Tuesday. ", { "entities" : 
             [(11,23,"train-destination"),(45,66,"train-departure")]
             }
    ),( 
        "The allenbell is a guesthouse located in the east. It is a cheap 4 star hotel with free parking and internet. ", { "entities" : 
             [(0,13,"hotel-name"),(19,29, "hotel-type"), (38,49, "area"), (59,63,"price-range"), (65,71,"hotel-stars"),(83,95,"hotel-parking")]
             }
    ),( 
        "I'll be leaving from Cambridge on Tuesday. I'd like to get to Leicester by 18:00 please. ", { "entities" : 
             [(16,30,"train-departure"),(31,41,"day"),(59,71,"train-destination"),(72,80,"train-arrive-by")]
             }
    ),( 
        "How about the moderately priced Anatolia?  The address is 30 Bridge Street, cb21uj. Would you like me to book that? ", { "entities" : 
             [(14,31,"price-range"),(32,40,"restaurant-name")]
             }
    ),( 
        "ok i would like to book it for thursday for 2 people  for 3 night im also looking for a restaurant in the same price range as the hotel  ", { "entities" : 
             [(27,39,"day"),(40,53,"hotel-book-people"),(54,65,"hotel-book-stay")]
             }
    ),( 
        "I have 9 different places for you. Do you prefer a guesthouse or hotel? ", { "entities" : 
             [(51,61,"hotel-type"),(65,70,"hotel-type")]
             }
    ),( 
        "1 person for 3 nights, please. I'll arrive on Tuesday.", { "entities" : 
             [(0,8,"hotel-book-people"),(13,21,"hotel-book-stay"),(46,53,"day")]
             }
    ),( 
        "I would like to book a room at the Worth House. ", { "entities" : 
             [(31,46,"hotel-name")]
             }
    ),( 
        "I will depart at Birmingham New Street and should arrive by 11:30. Can you help me with this? ", { "entities" : 
             [(14,38,"train-departure"),(57,65,"train-arrive-by")]
             }
    ),( 
        "Great.  I booked six tickets on TR4095 departing at 11:35 and arriving in cambridge at 11:52.  Your confirmation number is W6PWPYOP.  ", { "entities" : 
             [(17,29,"train-book-people"),(49,57,"train-leave-at"),(71,83,"train-destination"),(84,92,"train-arrive-by")]
             }
    ),( 
        "I need to book a train for Monday from Ely to Cambridge to arrive by 14:00 for 6 people. ", { "entities" : 
             [(23,33,"day"),(34,42,"train-departure"),(43,55,"train-destination"),(66,74,"train-arrive-by"), (79,87,"train-book-people")]
             }
    ),( 
        "I would like something in the center. Would you give me the name of the guesthouse, please? ", { "entities" : 
             [(72,82,"hotel-type"),(23,36,"area")]
             }
    ),( 
        "No I will take care of the train booking. I still need help finding an expensive 4 star hotel with free parking. I would prefer a guesthouse type. ", { "entities" : 
             [(81,87,"hotel-stars"),(71,80,"price-range"),(99,111,"hotel-parking"),(130,140,"hotel-type")]
             }
    ),( 
        "Certainly, the departure times are 05:29, 07:29, 09:29, 11:29, 13:29 ", { "entities" : 
             [(35,40,"train-leave-at"),(42,47,"train-leave-at"),(49,54,"train-leave-at"),(56,62,"train-leave-at"),(63,68,"train-leave-at")]
             }
    ),( 
        "No.  I need a train that departs Bishops Stortford on Wednesday, please.  ", { "entities" : 
             [(33,50,"train-departure"),(51,63,"day")]
             }
    ),( 
        "Yes cityroomz is a zero star hotel.", { "entities" : 
             [(4,13,"hotel-name"),(19,28,"hotel-stars")]
             }
    ),( 
        "There is one hotel under that criteria by the name of cityroomz, would you like more information or a booking? ", { "entities" : 
             [(54,63,"hotel-name")]
             }
    ),( 
        "That sounds great. I will need 7 tickets please!  ", { "entities" : 
             [(31,40,"train-book-people")]
             }
    ),( 
        "TR7578 will leave at 11:11 and arrive at Cambridge at 11:58. Is that okay? Would you like to book a ticket right now?", { "entities" : 
             [(18,26,"train-leave-at")]
             }
    ),( 
        "I have train TR0916 that will leave at 07:40 and will arrive at the airport at 08:08. Will that work for you? ", { "entities" : 
             [(36,44,"train-leave-at"),(64,75,"train-destination"),(76,84,"train-arrive-by")]
             }
    ),( 
        "Hi there, please find me a restaurant on the East side that serves russian food ", { "entities" : 
             [(67,84,"restaurant-food"),(38,54,"area")]
             }
    ),( 
        "can you book me 3 tickets please? ", { "entities" : 
             [(16,25,"train-book-people")]
             }
    ),( 
        "I want to get to London Kings Crossing.  ", { "entities" : 
             [(14,38,"train-destination")]
             }
    ),( 
        "i am looking for a restaurant that serves african food and is moderately priced ", { "entities" : 
             [(42,54,"restaurant-food"),(62,79,"price-range")]
             }
    ),( 
        "We have 9 expensive Chinese restaurants across town. Do you prefer a specific area of town? ", { "entities" : 
             [(10,19,"price-range"),(20,39,"restaurant-food")]
             }
    ),( 
        "I would like to book a taxi to leave after 11:45 to go to king's college. ", { "entities" : 
             [(37,48,"taxi-leave-at"),(58,72,"taxi-destination")]
             }
    ),( 
        "I need some information on taking a train from Kings Lynn to Cambridge", { "entities" : 
             [(42,57,"train-departure"),(58,70,"train-destination")]
             }
    ),( 
        "Wednesday, and can you please make sure I get there before 19:00.", { "entities" : 
             [(0,9,"day"),(52,64,"train-arrive-by")]
             }
    ),( 
        "The last train with ID TR3677 departing kings lynn to Cambridge on Wednesday will be the best option for you. It will depart by 17:11 and arrive by 17:58", { "entities" : 
             [(40,50,"train-departure"),(51,63,"train-destination"),(67,76,"day"),(125,133,"train-leave-at"),(145,153,"train-arrive-by")]
             }
    ),( 
        "Thank you. I am also looking for a multiple sports type attraction in the town centre. Can you tell me what is available?", { "entities" : 
             [(35,50,"attraction-type"),(67,85,"area")]
             }
    ),( 
        "what about the type of a museum?", { "entities" : 
             [(25,31,"attraction-type")]
             }
    ),( 
        "The Broughton House Gallery has the postcode cb11ln", { "entities" : 
             [(0,27,"attraction-name")]
             }
    ),( 
        "I want to get to Cambridge by 10:15.", { "entities" : 
             [(14,26,"train-destination"),(27,34,"taxi-arrive-by")]
             }
    ),( 
        "Can you reserve me a taxi that arrives to the restaurant before 14:00 on wednesday?", { "entities" : 
             [(57,69,"taxi-arrive-by"),(73,82,"day")]
             }
    ),
]

##### generate only from training set

In [65]:
result1= open("Using_custom_spaCy/chatito/chatito_data.txt","w+")
result2= open("Using_custom_spaCy/chatette/chatette_data.txt","w+")
f = open("nlp.json", "w+")
r1 = open("Using_custom_spaCy/chatito/chatito_data.txt", "r+")  
r2 = open("Using_custom_spaCy/chatette/chatette_data.txt", "r+")
f = open("nlp.json", "r+")
r1.write("\n")
r2.write("\n")
x=""
y=""
for text, annotations in Train_data:
    
    for ent in annotations.get('entities'):
        #print(ent[2])
        x=ent[0]
        y=ent[1]
        #print(text[x:y])

        r1 = open("Using_custom_spaCy/chatito/chatito_data.txt", "r+")  
        r2 = open("Using_custom_spaCy/chatette/chatette_data.txt", "r+")
        f = open("nlp.json", "r+")
        if ent[2] in f.read():
            f.write(" , \"" + text[x:y] + "\" ")
        else: 
            f.write("\n")
            f.write("{ \""+ent[2]+"\": { \" "+text[x:y] + "\" ")

                #using chatette format
        if ent[2] in r2.read():
            r2.write("|"+text[x:y])
        else:
            r2.write("\n")
            r2.write("\n")
            r2.write(" ~["+ent[2]+"]\n")
            r2.write("    "+text[x:y])
                 #using chatito format
        if ent[2] in r1.read():
            r1.write("    "+text[x:y]+"\n")
        else: 
            r1.write("\n")
            r1.write("\n")
            r1.write("~["+ent[2]+"]\n")
            r1.write("    "+text[x:y]+"\n")

### Training

In [50]:
new_model=""
Trained_model = ("Trained_model")
def main_train(model=None, output_dir=r'model', n_iter=100):
    """Load the model, set up the pipeline and train the entity recognizer."""
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank("en")  # create blank Language class
        print("Created blank 'en' model")

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if 'ner' not in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, last=True)

    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for _, annotations in Train_data:
         for ent in annotations.get('entities'):
            ner.add_label(ent[2])
            
    #for i in my_ent:
     #   ner.add_label(i)

    # get names of other pipes to disable them during training
    #other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    #with nlp.disable_pipes(*other_pipes):  # only train NER
        # reset and initialize the weights randomly – but only if we're
        # training a new model
    if model is None:
        optimize=nlp.begin_training()
    else:
        optimize= nlp.resume_training()
    #if model is None:
     #   optimizer = nlp.begin_training()
    #else:
     #   optimizer = nlp.entity.create_optimizer()
    
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    with nlp.disable_pipes(*other_pipes):  # only train NER

        for itn in range(n_iter):
            print("Starting iteration" + str(itn))
            random.shuffle(Train_data)
            losses = {}
            # batch up the examples using spaCy's minibatch
            batches = minibatch(Train_data, size=compounding(4.0, 32.0, 1.001))
            for batch in batches:
                texts, annotations = zip(*batch)
                nlp.update(
                texts,  # batch of texts
                annotations,  # batch of annotations
                sgd= optimize,
                drop=0.2,  # dropout - make it harder to memorise data
                losses=losses,
                )
                
            print("Losses", losses)
    new_model=nlp
    # test the trained model
    for text, _ in Train_data:
        doc = nlp(text)
        print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
        print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])
        displacy.render(doc, jupyter=True, style='ent')
        
    # save model to output directory
  
    nlp.to_disk(Trained_model)
    print("Saved model to", Trained_model)
main_train(model=None, output_dir=r'model', n_iter=100)

Created blank 'en' model
Starting iteration0
Losses {'ner': 953.988364214978}
Starting iteration1
Losses {'ner': 502.7145170375006}
Starting iteration2
Losses {'ner': 425.323807617533}
Starting iteration3
Losses {'ner': 410.33926007855916}
Starting iteration4
Losses {'ner': 496.97595727001317}
Starting iteration5
Losses {'ner': 403.5535069760377}
Starting iteration6
Losses {'ner': 345.5296486006846}
Starting iteration7
Losses {'ner': 363.86752905537287}
Starting iteration8
Losses {'ner': 320.58443804637636}
Starting iteration9
Losses {'ner': 255.5113605633292}
Starting iteration10
Losses {'ner': 278.7010588595788}
Starting iteration11
Losses {'ner': 238.89596787618973}
Starting iteration12
Losses {'ner': 211.35649896701125}
Starting iteration13
Losses {'ner': 155.38166653854148}
Starting iteration14
Losses {'ner': 159.1943600062636}
Starting iteration15
Losses {'ner': 117.17228893301026}
Starting iteration16
Losses {'ner': 123.83177536238544}
Starting iteration17
Losses {'ner': 93.0079

Entities [('by 14:45', 'taxi-arrive-by')]
Tokens [('I', '', 2), ('would', '', 2), ('like', '', 2), ('a', '', 2), ('taxi', '', 2), ('from', '', 2), ('the', '', 2), ('hotel', '', 2), ('to', '', 2), ('the', '', 2), ('restaurant', '', 2), ('.', '', 2), ('I', '', 2), ('would', '', 2), ('like', '', 2), ('to', '', 2), ('arrive', '', 2), ('by', 'taxi-arrive-by', 3), ('14:45', 'taxi-arrive-by', 1), ('.', '', 2), ('I', '', 2), ('would', '', 2), ('like', '', 2), ('the', '', 2), ('contact', '', 2), ('number', '', 2), ('and', '', 2), ('car', '', 2), ('type', '', 2)]


Entities [('to Cambridge', 'train-destination'), ('from stansted airport', 'train-departure')]
Tokens [('I', '', 2), ('am', '', 2), ('going', '', 2), ('to', 'train-destination', 3), ('Cambridge', 'train-destination', 1), ('and', '', 2), ('i', '', 2), ('plan', '', 2), ('to', '', 2), ('depart', '', 2), ('from', 'train-departure', 3), ('stansted', 'train-departure', 1), ('airport', 'train-departure', 1), ('and', '', 2), ('i', '', 2), ('need', '', 2), ('a', '', 2), ('train', '', 2), ('schedule', '', 2), ('from', '', 2), ('stansted', '', 2), ('airport', '', 2), ('that', '', 2), ('will', '', 2), ('get', '', 2), ('to', '', 2), ('Cambridge', '', 2), ('by', '', 2), ('13:30', '', 2), ('Tuesday', '', 2), ('.', '', 2)]


Entities [('at birmingham new street', 'train-destination'), ('by 8:44', 'train-arrive-by')]
Tokens [('TR4300', '', 2), ('will', '', 2), ('arrive', '', 2), ('at', 'train-destination', 3), ('birmingham', 'train-destination', 1), ('new', 'train-destination', 1), ('street', 'train-destination', 1), ('by', 'train-arrive-by', 3), ('8:44', 'train-arrive-by', 1), ('.', '', 2), ('Would', '', 2), ('you', '', 2), ('like', '', 2), ('to', '', 2), ('book', '', 2), ('a', '', 2), ('ticket', '', 2), ('?', '', 2)]


Entities [('the gardenia', 'restaurant-name'), ('la mimosa', 'restaurant-name')]
Tokens [('I', '', 2), ("'ve", '', 2), ('got', '', 2), ('three', '', 2), ('that', '', 2), ('fit', '', 2), ('that', '', 2), ('bill', '', 2), ('...', '', 2), ('the', 'restaurant-name', 3), ('gardenia', 'restaurant-name', 1), (',', '', 2), ('la', 'restaurant-name', 3), ('mimosa', 'restaurant-name', 1), (',', '', 2), ('and', '', 2), ('shiraz', '', 2), ('.', '', 2), (' ', '', 2), ('Do', '', 2), ('you', '', 2), ('have', '', 2), ('a', '', 2), ('preference', '', 2), ('?', '', 2)]


...

Entities [('2 tickets', 'train-book-people')]
Tokens [('Yes', '', 2), (',', '', 2), ('could', '', 2), ('you', '', 2), ('book', '', 2), ('me', '', 2), ('2', 'train-book-people', 3), ('tickets', 'train-book-people', 1), ('and', '', 2), ('get', '', 2), ('me', '', 2), ('a', '', 2), ('reference', '', 2), ('number', '', 2), ('?', '', 2)]


Entities [('in the center', 'area'), ('guesthouse', 'hotel-type')]
Tokens [('I', '', 2), ('would', '', 2), ('like', '', 2), ('something', '', 2), ('in', 'area', 3), ('the', 'area', 1), ('center', 'area', 1), ('.', '', 2), ('Would', '', 2), ('you', '', 2), ('give', '', 2), ('me', '', 2), ('the', '', 2), ('name', '', 2), ('of', '', 2), ('the', '', 2), ('guesthouse', 'hotel-type', 3), (',', '', 2), ('please', '', 2), ('?', '', 2)]


Entities [('six tickets on', 'restaurant-book-people'), ('at 11:35', 'train-leave-at'), ('in cambridge', 'train-destination'), ('at 11:52', 'train-arrive-by')]
Tokens [('Great', '', 2), ('.', '', 2), (' ', '', 2), ('I', '', 2), ('booked', '', 2), ('six', 'restaurant-book-people', 3), ('tickets', 'restaurant-book-people', 1), ('on', 'restaurant-book-people', 1), ('TR4095', '', 2), ('departing', '', 2), ('at', 'train-leave-at', 3), ('11:35', 'train-leave-at', 1), ('and', '', 2), ('arriving', '', 2), ('in', 'train-destination', 3), ('cambridge', 'train-destination', 1), ('at', 'train-arrive-by', 3), ('11:52', 'train-arrive-by', 1), ('.', '', 2), (' ', '', 2), ('Your', '', 2), ('confirmation', '', 2), ('number', '', 2), ('is', '', 2), ('W6PWPYOP', '', 2), ('.', '', 2), (' ', '', 2)]


Entities [('cheap place to dine', 'price-range'), ('in the centre', 'area')]
Tokens [('Hello', '', 2), (',', '', 2), ('I', '', 2), ('am', '', 2), ('looking', '', 2), ('for', '', 2), ('a', '', 2), ('cheap', 'price-range', 3), ('place', 'price-range', 1), ('to', 'price-range', 1), ('dine', 'price-range', 1), ('in', 'area', 3), ('the', 'area', 1), ('centre', 'area', 1)]


Saved model to Trained_model


### Testing the model

In [51]:
def test_model(nlp):
    texts = [
        "I'm looking for a 4 star hotel.",
        "I've found 21 4 star hotels. Is there a certain area you want to stay in?",
        "Yes, in the east, please.",
        "I have found several hotels. Do you have any preference towards price?",
        "I would not mind finding one with free wifi.",
        "Unfortunately, we don't have any hotels with those preference in the area, but we do have 6 guesthouses available. Would a guesthouse be okay?",
        "A guesthouse is fine. Which one would you recommend?",
        "I recommend the Leverton House. It's a cheap guesthouse, but still a 4-star establishment.",
        "That sounds good.  Can you give me the address and postcode for Leverton House?",
        "They are located at 732-734 newmarket road, and postcode is cb58rs",
        "Thank you. I'm also looking for a venetian restaurant on the east side as well.", 
        "I'm sorry there are no Venetian restaurants. Are there any cuisines I can look for?",
        "Yes, how about one that serves Indian food?",
        "There are four restaurants that serve indian food in the east. Do you have a price range?",
        "Book one of them for 8 people at 14:15 on tuesday.",
        "Alright, I have you booked at Curry Prince. Your reference number is: 55UNFF8Z. Anything else I can do for you today?",
        "Yes, can you schedule a taxi to take me from Leverton House to Curry Prince? I need to get there by 14:15. ",
        "Okay, your taxi car type is a white bmw and the contact number is 07967879848. Is there anything else you need?",
        "That is all.  Thank you",
        "Yes I would like to book the train for 4 people and I'll need the reference number please.",
        "I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?",
        "Great, could I book a table of 5 for 11:30 on wednesday?",
    ]
    print("Loading from", Trained_model)
    nlp2 = spacy.load(Trained_model)
    docs = nlp2.pipe(texts)
    for doc in docs:
        print(doc.text)
        print([(t.text, t.dep_, t.head.text) for t in doc if t.dep_ != "-"])
        displacy.render(doc, jupyter=True, style='ent')

In [52]:
test_model(nlp)

Loading from Trained_model
I'm looking for a 4 star hotel.
[('I', '', 'I'), ("'m", '', "'m"), ('looking', '', 'looking'), ('for', '', 'for'), ('a', '', 'a'), ('4', '', '4'), ('star', '', 'star'), ('hotel', '', 'hotel'), ('.', '', '.')]


I've found 21 4 star hotels. Is there a certain area you want to stay in?
[('I', '', 'I'), ("'ve", '', "'ve"), ('found', '', 'found'), ('21', '', '21'), ('4', '', '4'), ('star', '', 'star'), ('hotels', '', 'hotels'), ('.', '', '.'), ('Is', '', 'Is'), ('there', '', 'there'), ('a', '', 'a'), ('certain', '', 'certain'), ('area', '', 'area'), ('you', '', 'you'), ('want', '', 'want'), ('to', '', 'to'), ('stay', '', 'stay'), ('in', '', 'in'), ('?', '', '?')]


Yes, in the east, please.
[('Yes', '', 'Yes'), (',', '', ','), ('in', '', 'in'), ('the', '', 'the'), ('east', '', 'east'), (',', '', ','), ('please', '', 'please'), ('.', '', '.')]


I have found several hotels. Do you have any preference towards price?
[('I', '', 'I'), ('have', '', 'have'), ('found', '', 'found'), ('several', '', 'several'), ('hotels', '', 'hotels'), ('.', '', '.'), ('Do', '', 'Do'), ('you', '', 'you'), ('have', '', 'have'), ('any', '', 'any'), ('preference', '', 'preference'), ('towards', '', 'towards'), ('price', '', 'price'), ('?', '', '?')]


I would not mind finding one with free wifi.
[('I', '', 'I'), ('would', '', 'would'), ('not', '', 'not'), ('mind', '', 'mind'), ('finding', '', 'finding'), ('one', '', 'one'), ('with', '', 'with'), ('free', '', 'free'), ('wifi', '', 'wifi'), ('.', '', '.')]


...

Okay, your taxi car type is a white bmw and the contact number is 07967879848. Is there anything else you need?
[('Okay', '', 'Okay'), (',', '', ','), ('your', '', 'your'), ('taxi', '', 'taxi'), ('car', '', 'car'), ('type', '', 'type'), ('is', '', 'is'), ('a', '', 'a'), ('white', '', 'white'), ('bmw', '', 'bmw'), ('and', '', 'and'), ('the', '', 'the'), ('contact', '', 'contact'), ('number', '', 'number'), ('is', '', 'is'), ('07967879848', '', '07967879848'), ('.', '', '.'), ('Is', '', 'Is'), ('there', '', 'there'), ('anything', '', 'anything'), ('else', '', 'else'), ('you', '', 'you'), ('need', '', 'need'), ('?', '', '?')]


That is all.  Thank you
[('That', '', 'That'), ('is', '', 'is'), ('all', '', 'all'), ('.', '', '.'), (' ', '', ' '), ('Thank', '', 'Thank'), ('you', '', 'you')]


Yes I would like to book the train for 4 people and I'll need the reference number please.
[('Yes', '', 'Yes'), ('I', '', 'I'), ('would', '', 'would'), ('like', '', 'like'), ('to', '', 'to'), ('book', '', 'book'), ('the', '', 'the'), ('train', '', 'train'), ('for', '', 'for'), ('4', '', '4'), ('people', '', 'people'), ('and', '', 'and'), ('I', '', 'I'), ("'ll", '', "'ll"), ('need', '', 'need'), ('the', '', 'the'), ('reference', '', 'reference'), ('number', '', 'number'), ('please', '', 'please'), ('.', '', '.')]


I've got three that fit that bill... the gardenia, la mimosa, and shiraz.  Do you have a preference?
[('I', '', 'I'), ("'ve", '', "'ve"), ('got', '', 'got'), ('three', '', 'three'), ('that', '', 'that'), ('fit', '', 'fit'), ('that', '', 'that'), ('bill', '', 'bill'), ('...', '', '...'), ('the', '', 'the'), ('gardenia', '', 'gardenia'), (',', '', ','), ('la', '', 'la'), ('mimosa', '', 'mimosa'), (',', '', ','), ('and', '', 'and'), ('shiraz', '', 'shiraz'), ('.', '', '.'), (' ', '', ' '), ('Do', '', 'Do'), ('you', '', 'you'), ('have', '', 'have'), ('a', '', 'a'), ('preference', '', 'preference'), ('?', '', '?')]


Great, could I book a table of 5 for 11:30 on wednesday?
[('Great', '', 'Great'), (',', '', ','), ('could', '', 'could'), ('I', '', 'I'), ('book', '', 'book'), ('a', '', 'a'), ('table', '', 'table'), ('of', '', 'of'), ('5', '', '5'), ('for', '', 'for'), ('11:30', '', '11:30'), ('on', '', 'on'), ('wednesday', '', 'wednesday'), ('?', '', '?')]


In [53]:
print("Loading from", Trained_model)
nlp2 = spacy.load(Trained_model)
doc = nlp2("3 nights, 3 people, please.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from Trained_model
Entities [('3 nights', 'hotel-book-stay'), ('3 people', 'hotel-book-people')]


In [54]:
print("Loading from", Trained_model)
nlp2 = spacy.load(Trained_model)
doc = nlp2("Do they have free parking? If so, please reserve a room for Tuesday for 7 people, 4 nights.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from Trained_model
Entities [('free parking', 'hotel-parking'), ('for Tuesday', 'day'), ('for 7 people', 'hotel-book-people'), ('4 nights', 'hotel-book-stay')]


In [55]:
print("Loading from", Trained_model)
nlp2 = spacy.load(Trained_model)
doc = nlp2("I want to reserve a room for 4 nights.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from Trained_model
Entities [('for 4 nights.', 'train-arrive-by')]


In [56]:
print("Loading from", Trained_model)
nlp2 = spacy.load(Trained_model)
doc = nlp2("Hello, I am looking for some places to go in the centre of town. There is a lot to do in the centre. Is there a certain type of attraction you'd like to see or do? I was thinking something related to multiple sports We don't have any multiple sports facilities in the centre of town. Do you want to look for something else? How about a theatre? I think we would enjoy seeing a show! May I recommend Cambridge Arts Theatre located in the centre of town? That would be great. Can I have the postcode, address, and entrance fee please? I don't have any information about admission, but you can call them to get more information.  The number is 01223503333. The address is 6 saint edward's passage cb23pj Ok.  I also need info on the restaurant Darrys cookhouse and wine shop. Darrys Cookhouse and Wine Shop is a modern European restaurant located in the centre of town.  It's in the expensive price range.  Would you like to make a reservation? Yes, that would be great. I'll need a table for 7 on Friday at 18:00.  Booking was successful. The table will be reserved for 15 minutes. Reference number is : BT75ESXM. Can I help you with anything else? I don't think so.  Thanks for all your help. Hope you have a great time during your trip. That was so nice of you to say thanks so much. You're very welcome! Take care!")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from Trained_model
Entities [('in the centre', 'area'), ('in the centre', 'area'), ('multiple sports', 'attraction-type'), ('multiple sports', 'attraction-type'), ('in the centre', 'area'), ('in the centre', 'area'), ('cookhouse', 'hotel-type'), ('wine', 'hotel-type'), ('Darrys Cookhouse and Wine Shop', 'restaurant-name'), ('modern European', 'restaurant-food'), ('in the centre', 'area'), ('expensive', 'price-range'), ('a table for 7', 'restaurant-book-people'), ('on Friday', 'day'), ('at 18:00.', 'restaurant-book-time'), ('The table', 'train-book-people'), ('be reserved', 'hotel-stars'), ("n't think", 'hotel-stars')]


In [57]:
print("Loading from", Trained_model)
nlp2 = spacy.load(Trained_model)
doc = nlp2("I am looking for the addresses of each of the moderately priced restaurants in the south part of town. The address for Pizza Hut Cherry Hinton is G4 Cambridge Leisure Park Clifton Way Cherry Hinton and the address for Restaurant Alimentum is 152 - 154 Hills Road. Is there anything else? There is restaurant alimentum which is a modern european restaurant located in the south part of town and is in the moderate price range. Could you give me the address for Restaurant Alimentum? Restaurant Alimentum's address is G4 Cambridge Leisure Park Clifton Way Cherry Hinton. May I help you with anything else? No thank you good bye Thank you for using our system. Goodbye.")
print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
displacy.render(doc,  style='ent')

Loading from Trained_model
Entities [('moderately priced', 'price-range'), ('in the south part of town', 'area'), ('Pizza Hut', 'attraction-name'), ('Cherry Hinton', 'restaurant-food'), ('G4 Cambridge', 'taxi-destination'), ('Leisure Park Clifton', 'hotel-book-stay'), ('Cherry Hinton', 'restaurant-name'), ('Restaurant Alimentum', 'taxi-destination'), ('alimentum which', 'hotel-internet'), ('modern european', 'restaurant-food'), ('in the south part of town', 'area'), ('in the moderate price range', 'price-range'), ('Alimentum', 'restaurant-name'), ("Restaurant Alimentum's address", 'restaurant-book-people'), ('G4 Cambridge', 'taxi-destination'), ('Leisure Park Clifton', 'area'), ('Cherry Hinton', 'restaurant-food')]


### Model evaluation

In [59]:
from spacy.scorer import Scorer 
from spacy.gold import GoldParse
new_model=spacy.load(Trained_model)
Test_data = [
    ( 
        "I have train TR0916 that will leave at 07:40 and will arrive at the airport at 08:08. Will that work for you? ", { "entities" : 
             [(36, 44, "train-leave-at"),(61,75,"train-destination"),(76,84, "train-arrive-by")]
             }
    ),( 
        "Hi there, please find me a restaurant on the East side that serves russian  food ", { "entities" : 
             [(38,54,"restaurant-area"),(67,80,"restaurant-food")]
             }
    ),( 
        "can you book me 3 tickets please? ", { "entities" : 
             [(16,25,"train-book-people")]
             }
    ),( 
        "I want to get to London Kings Crossing.  ", { "entities" : 
             [(14,45,"train-destination")]
             }
    ),( 
        "i am looking for a restaurant that serves african food and is moderately priced ", { "entities" : 
             [(42,45,"restaurant-food"),(62,81,"restaurant-price-range")]
             }
    ),(
        "Yes for 3 at 14:45 wednesday, can I get the reference number too please", { "entities" :
        [(4, 9, "restaurant-book-people"), (10, 18, "restaurant-book-time"), (19, 28, "day")]
        }
    ),( 
        "Both offer free parking and free wifi. The Alexander B&B is 4 star rated. The El Shaddai has a 0 rating.", { "entities" : 
             [(11, 23, "hotel-parking"), (28, 37, "hotel-internet"), (39, 56, "hotel-name"), (60, 66, "hotel-stars"), (74, 87, "hotel-name"), (95, 103, "hotel-stars")]
             }
    ),( 
        "3 nights, 3 people, please.", { "entities" : 
             [(0, 8, "hotel-book-stay"), (10, 18, "hotel-book-people")]
             }
    ),( 
        "I would like a taxi from the hotel to the restaurant. I would like to arrive by 14:45. I would like the contact number and car type",  { "entities" : 
             [(77, 85, "taxi-arrive-by")]
             }
    ),( 
        "Thanks. I also need a cheap place to stay in the center.", { "entities" : 
             [(22, 33, "price-range"),(42, 55, "area")]
             }
    ),( 
        "I am looking for info about a hotel called city centre north b and b. Can you help?", { "entities" : 
             [(43, 68, "hotel-name")]
             }
    ),( 
        "Yes. City Centre North B and B is a guesthouse in the north side of town, that has both free internet and parking. Do you want to book a room?", { "entities" : 
             [(5,30, "hotel-name"),(34, 46, "hotel-type"),(47, 72, "area")]
             }
    ),( 
        "Ok, I am also looking for a train from Cambridge to Bishops Stortford.", { "entities" : 
             [(34, 48, "train-departure"),(49, 69, "train-destination")]
             }
    ),
    
]
def evaluate(new_model, Test_data):
    scorer = Scorer()
    for text, metadata in Test_data:
        #print(text)
        doc_gold_text = new_model.make_doc(text)
        gold = GoldParse(doc_gold_text, entities=metadata['entities'])
        pred_value = new_model(text)
        scorer.score(pred_value, gold)
        
    return scorer.scores


test_result = evaluate(new_model, Test_data)
print (test_result)


{'las': 0.0, 'las_per_type': {'': {'f': 0.0, 'r': 0.0, 'p': 0.0}}, 'ents_p': 84.21052631578947, 'textcats_per_cat': {}, 'ents_per_type': {'train-leave-at': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'hotel-book-people': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'hotel-type': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'restaurant-area': {'f': 0.0, 'r': 0.0, 'p': 0.0}, 'train-book-people': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'hotel-name': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'area': {'f': 80.0, 'r': 100.0, 'p': 66.66666666666666}, 'restaurant-book-people': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'train-arrive-by': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'restaurant-book-time': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'taxi-arrive-by': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'restaurant-food': {'f': 0.0, 'r': 0.0, 'p': 0.0}, 'hotel-book-stay': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'train-destination': {'f': 50.0, 'r': 50.0, 'p': 50.0}, 'price-range': {'f': 100.0, 'r': 100.0, 'p': 100.0}, 'day': {'f': 100.0, 

In [ ]:
new_sentence=""
result1= open("Last_results/chatito/chatito_data.txt","w+")
result2= open("Last_results/chatette/chatette_data.txt","w+")
f= open("Last_results/nlp.json","w+")
r1 = open("Last_results/chatito/chatito_data.txt", "r+")  
r2 = open("Last_results/chatette/chatette_data.txt", "r+")
f= open("Last_results/nlp.json","r+")
r1.write("\n")
r2.write("\n")
for object_1 in dict_json_weighted: 
    for i in range(len(dict_json_weighted[object_1]['log'])):
        print(str(i)+"-"+dict_json_weighted[object_1]['log'][i]['text'])
        sentence =nlp2 (dict_json_weighted[object_1]['log'][i]['text'])
        ### create a file for each sentence in both directories 

        ### print the label
        #print("Verbs:", [token.lemma_ for token in sentence if token.pos_ == "VERB"])
        r1 = open("Last_results/chatito/chatito_data.txt", "r+")  
        r2 = open("Last_results/chatette/chatette_data.txt", "r+")
        f= open("Last_results/nlp.json","r+")

        for X in (sentence.ents) :
            print([(X.text, X.label_) ])

            r1 = open("Last_results/chatito/chatito_data.txt", "r+")  
            r2 = open("Last_results/chatette/chatette_data.txt", "r+")
            f= open("Last_results/nlp.json","r+")
            
            if ent[2] in f.read():
                f.write(" , \"" + text[x:y] + "\" ")
            else: 
                f.write("\n")
                f.write("{ \""+ent[2]+"\": { \" "+text[x:y] + "\" ")

                #using chatette format
            if X.label_ in r2.read():
                r2.write("|"+X.text)
            else:
                r2.write("\n")
                r2.write("\n")
                r2.write(" ~["+X.label_+"]\n")
                r2.write("   "+X.text)
                 #using chatito format
            if X.label_ in r1.read():
                r1.write("   "+X.text+"\n")
            else: 
                r1.write("\n")
                r1.write("\n")
                r1.write("~["+X.label_+"]\n")
                r1.write("   "+X.text+"\n")


        ### highlight named entities and their labels in a text
        displacy.render(sentence, jupyter=True, style='ent')




0-Hi, i need to book a taxi to go to funky fun house. I need to leave after 8:45. 
[('after 8:45', 'train-leave-at')]


1-Where will you leave from?
[('from', 'attraction-type')]


2-The taxi should depart from the cambridge punter
[('from the cambridge', 'train-departure')]


3-Alrighty. I have a grey ford for you with the contact number 07266756209. Anything else you need?


4-No thanks, just needed a taxi. Have a great day!


...

4-Ok, how about an expensive Italian restaurant around the centre?
[('expensive', 'price-range')]
[('Italian restaurant', 'restaurant-food')]
[('around the centre', 'area')]


5-Would you like to book don pasquale pizzeria? It matches all of your latest criteria.


6-Yes.  I'd also like their phone number please.


7-Don Pasquale Pizzeria's phone number is 01223350106, what date, time, and number of people would you like to book?


8-That's all the info I need on the pizzeria. I also need a train to leave after 20:15 and depart from stansted airport.
[('after 20:15', 'train-leave-at')]
